In [246]:
# import libraries

import json
import pandas as pd
import random
import numpy as np
import ast
from utils import load_filtered_data
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
from sklearn.neighbors import NearestNeighbors
from sklearn.metrics.pairwise import cosine_similarity
from surprise import Reader, Dataset, KNNBasic, accuracy, SVD
from surprise.model_selection import train_test_split
from collections import Counter, defaultdict

# Recommender System

### Libraries

### Dataset

In [247]:
# major variables

city = 'Springfield'
city_data = load_filtered_data(city)

In [248]:
# read communities

connection = 'priority_combined'
with open(f'communities/Springfield_{connection}_communities.json') as f:
    data = json.load(f)

data['communities']

[['IpLRJY4CP3fXtlEd8Y4GFQ',
  'RgDVC3ZUBqpEe6Y1kPhIpw',
  'om5ZiponkpRqUNa3pVPiRg',
  'KrIL3TIOJI-tjvU6BlcA-g',
  '1sGYXSkJHPhJ6wQtc-RbZw',
  'OgYi5x02MBukfxPNFe1ePg',
  'SH-GRUQlUZTco0ofRbwVdQ',
  'GG0mFsEXb-02_dzFPqRV1Q',
  'k_muz40jJaiY1PVga6NDXA',
  'SdlozylmEKkBW910mGw1dQ',
  'FyiYuZrIzSkgshdazHZCWw',
  'nBdv5Br4G8pDWXXqSXhUug',
  'g0_x4kVvJAYuk96oCcbOmw',
  'CHeMEder5ijEoCPLWjto_Q',
  '_BcWyKQL16ndpBdggh2kNA',
  'cUk4n3GMShdIr5pLyt9PFQ',
  'HZRfI9weev2Vr_w0jPF8-Q',
  'kaHmTcEoVS3oQvfJfDe8kg',
  'upQwDazroow3rjNMW4PZww',
  'IPxJLWpKptzpTWlfjFiuHA',
  'YAIxImxlu3jlSdG91T2Pig',
  'yi8MUcO3O6ALXErrFuj2_A',
  '4P8qDuDy3C8s6Rkm5wEI4Q',
  '-hKniZN2OdshWLHYuj21jQ',
  'XwbnUSJeDscLDGfe4A1x3Q',
  'bEC8C904SPszVpMPEUKFNA',
  'rP--R1kPGdiFlQo_CP6LzA',
  'krs31wGmvy1OHr9556aWyg',
  '84HvpQDxcHWmbMDfs8IEYw',
  'w0Eb3PnZFiyQdWqXYKnx3A',
  '3PB1TY8e8NnnHBHTb96p7Q',
  'sanxwhDER9eW3gTPWpmS0Q',
  'JTqQ9C9S2Qc8_aHtO1965g',
  'Oi1qbcz2m2SnwUeztGYcnQ',
  '8MKygqfspKqG2-X9ycR-Ow',
  'CDMDkgXB8kdo3DASM

In [249]:
merged = pd.merge(city_data['review'], city_data['user'], on='user_id', how='left')
merged = pd.merge(merged, city_data['business'], on='business_id', how='left')
merged = merged.drop_duplicates(subset=['user_id', 'business_id'])

merged.rename(columns={'stars_x': 'rating'}, inplace=True)


In [250]:
def convert_to_binary(value):
    if isinstance(value, str) and (value.lower() == 'true' or value.lower() == "u'free'" or value.lower() == "'free'" or value.lower() == "'casual'" 
                                   or value.lower() == "u'full_bar'" or value.lower() == "u'beer_and_wine'" or value.lower() == "u'outdoor'"
                                   or value.lower() == "'outdoor'" or value.lower() == "'full_bar'"):
        return 1
    elif isinstance(value, str) and value.lower() == 'false':
        return 0
    elif isinstance(value, str) and (value.lower() == 'nan' or value.lower() == 'none'):
        return 0
    elif isinstance(value, str) and (value.lower() == "u'no'" or value.lower() == "u'casual'" or value.lower() == "u'none'" or value.lower() == "u'paid'"):
        return 0
    elif isinstance(value, str) and (value.lower().strip("'") == 'no' or value.lower().strip("'") == 'none'):
        return 0
    return value

In [251]:
# for index, row in merged.iterrows():
#     try:
#         attributes_dict = ast.literal_eval(row['attributes'])
#     except ValueError:
#         continue
#     merged.fillna(0, inplace=True)
#     merged.replace('None', 0, inplace=True)
#     for key, value in attributes_dict.items():
#         attributes_dict[key] = convert_to_binary(value)
        
#         if attributes_dict[key] is not None:  
#             merged.at[index, key] = attributes_dict[key]
#         else:
#             merged.at[index, key] = 0 
#     merged.at[index, 'attributes'] = attributes_dict

# merged.drop('attributes', axis=1, inplace=True)

all_categories = set()
    
# Iterate through each row and add categories to the set
for categories_list in merged['categories']:
    x = categories_list.split(',')
    for i in x:
        all_categories.add(i.strip())

# Create a column for each unique category
for category in all_categories:
    merged[category] = 0

# Iterate through each row and set the corresponding category column to 1 if present in categories list
for i, row in merged.iterrows():
    for category in row['categories']:
        print(category)
        merged.at[i, category] = 1

# Drop the original 'categories' column
merged.drop('categories', axis=1, inplace=True)
merged.drop('attributes', axis=1, inplace=True)

print(merged.columns)
merged.to_csv("merged_categories.csv", index=False)

/tmp/ipykernel_19986/3594855909.py:29: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`
  merged[category] = 0


H
o
m
e
 
S
e
r
v
i
c
e
s
,
 
H
o
m
e
 
&
 
G
a
r
d
e
n
,
 
B
u
i
l
d
i
n
g
 
S
u
p
p
l
i
e
s
,
 
A
p
p
l
i
a
n
c
e
s
,
 
M
a
t
t
r
e
s
s
e
s
,
 
A
p
p
l
i
a
n
c
e
s
 
&
 
R
e
p
a
i
r
,
 
H
a
r
d
w
a
r
e
 
S
t
o
r
e
s
,
 
S
h
o
p
p
i
n
g
,
 
F
u
r
n
i
t
u
r
e
 
S
t
o
r
e
s
,
 
O
u
t
l
e
t
 
S
t
o
r
e
s
,
 
L
o
c
a
l
 
S
e
r
v
i
c
e
s
,
 
P
l
u
m
b
i
n
g
,
 
S
h
o
p
p
i
n
g
 
C
e
n
t
e
r
s
R
e
s
t
a
u
r
a
n
t
s
,
 
N
i
g
h
t
l
i
f
e
,
 
B
a
r
s
,
 
S
a
n
d
w
i
c
h
e
s
,
 
D
i
v
e
 
B
a
r
s
S
p
o
r
t
s
 
B
a
r
s
,
 
B
a
r
s
,
 
A
m
e
r
i
c
a
n
 
(
N
e
w
)
,
 
A
m
e
r
i
c
a
n
 
(
T
r
a
d
i
t
i
o
n
a
l
)
,
 
R
e
s
t
a
u
r
a
n
t
s
,
 
N
i
g
h
t
l
i
f
e
,
 
S
e
a
f
o
o
d
R
e
s
t
a
u
r
a
n
t
s
,
 
N
i
g
h
t
l
i
f
e
,
 
B
a
r
s
,
 
S
a
n
d
w
i
c
h
e
s
,
 
D
i
v
e
 
B
a
r
s
S
u
s
h
i
 
B
a
r
s
,
 
R
e
s
t
a
u
r
a
n
t
s
,
 
R
a
m
e
n
,
 
S
t
e
a
k
h
o
u
s
e
s
,
 
J
a
p
a
n
e
s
e
,
 
N
o
o
d
l
e
s
B
a
r
s
,
 
N
i
g
h
t
l
i
f
e
,
 
L
o
u
n
g
e
s
,
 
S
t
e
a
k
h
o
u
s
e
s
,
 
R
e
s
t
a
u
r
a
n
t
s


### Train and test sets

In [ ]:
community_trainsets = {}
community_testsets = {}

communities = {}

for idx, community_users in enumerate(data['communities']):
    communities[idx] = community_users

for community_id, community in communities.items():    
    community_reviews = merged[merged['user_id'].isin(community)]
    user_review_counts = merged.groupby('user_id').size()
    user_review_counts = user_review_counts.reset_index()
    user_review_counts.columns = ['user_id', 'review_count']

    users_with_min_reviews = user_review_counts[user_review_counts['review_count'] >= 3]['user_id'].tolist()

    merged_filtered = merged[merged['user_id'].isin(users_with_min_reviews)]

    trainset = defaultdict(list)
    testset = defaultdict(list)
    for user_id, group in merged_filtered.groupby('user_id'):
        num_reviews = len(group)
        train_size = int(num_reviews * 0.8)
        train_reviews = group[:train_size]  # Select the first 80% of reviews
        test_reviews = group.iloc[train_size:] 
        trainset[community_id].extend(train_reviews.values.tolist())
        testset[community_id].extend(test_reviews.values.tolist())

    # reader = Reader(rating_scale=(1, 5))
    # train_data = Dataset.load_from_df(pd.DataFrame(trainset[community_id]), reader)
    # test_data = Dataset.load_from_df(pd.DataFrame(testset[community_id]), reader)

    # community_trainsets[community_id] = train_data.build_full_trainset()
    # community_testsets[community_id] = test_data.build_full_trainset().build_testset()




### Helper methods

In [ ]:
def evaluate_algorithm(algo, trainset, testset):
    '''
    Evaluate the performance of the algorithm
    '''
    algo.fit(trainset)
    predictions = algo.test(testset)
   
    rmse = accuracy.rmse(predictions)
    return rmse

In [ ]:
def content_based_recommendations(community, trainset, top_n=5):
    community_reviews = trainset[trainset['user_id'].isin(community)]

    business_data = trainset[['user_id', 'business_id', 'rating']].drop_duplicates()
 
    similarity_matrix = cosine_similarity(trainset[[
        'rating', 'RestaurantsPriceRange2','ByAppointmentOnly', 'BusinessAcceptsCreditCards', 'WiFi', 
        'GoodForKids','RestaurantsReservations','RestaurantsTakeOut','BikeParking', 'Caters','RestaurantsAttire', 
        'RestaurantsGoodForGroups','HasTV','OutdoorSeating','DogsAllowed','WheelchairAccessible', 
        'RestaurantsTableService', 'RestaurantsDelivery','HappyHour', 'Corkage','BusinessAcceptsBitcoin','CoatCheck', 'DriveThru'
    ]])

    community_recommendations = {}

    for user_id in community:
        reviewed_businesses = community_reviews[community_reviews['user_id'] == user_id]['business_id'].unique()
        reviewed_indices = [i for i, bid in enumerate(trainset['business_id']) if bid in reviewed_businesses]
        avg_similarity = similarity_matrix[:, reviewed_indices].mean(axis=1)
        top_indices = avg_similarity.argsort()[-top_n:][::-1]
        top_recommendations = business_data.iloc[top_indices]['business_id'].tolist()
        community_recommendations[user_id] = top_recommendations
    return community_recommendations

In [ ]:
community_recommendations = {}
count = 0
id = 0
for community_id, community in communities.items():
    # recommendation = get_community_recommendations(community, merged)
    recommendation = content_based_recommendations(community, trainset)
    if recommendation is not None:
        community_recommendations[community_id] = recommendation


#### User-Based

In [ ]:
# user-based collaborative filtering for each community


ubcf_algo = KNNBasic(sim_options={'user_based': True})
user_recommendations = {}

for community_id, trainset in community_trainsets.items():
    testset = community_testsets[community_id]
    # ubcf_rmse = evaluate_algorithm(ubcf_algo, trainset, testset)
    ubcf_algo.fit(trainset)
    predictions = ubcf_algo.test(testset)

    for uid, iid, true_r, est, _ in predictions:
        if uid not in user_recommendations:
            user_recommendations[uid] = []
        user_recommendations[uid].append((iid, est))

    for uid, ratings in user_recommendations.items():
        ratings.sort(key=lambda x: x[1], reverse=True)
        
        top_n_recommendations = {}
        for uid, ratings in user_recommendations.items():
            top_n_recommendations[uid] = [iid for iid, _ in ratings[:5]]
        
    print(top_n_recommendations)



In [ ]:
'''
Join the user-based and content-based recommendations
'''
def join_recommendations(user_based, content_based, num_of_recommendations=5):

    hybrid_recommendations = {}

    for user_id in user_based:
        user_based_rec = user_based[user_id]
        content_based_rec = content_based[user_id]

        combined_rec = []

        common_businesses = set([rec[0] for rec in user_based_rec]).intersection(set([rec[0] for rec in content_based_rec]))
        for rec in user_based_rec:
            if rec[0] in common_businesses:
                combined_rec.append(rec)

        for rec in user_based_rec:
            if rec[0] not in common_businesses and len(combined_rec) < num_of_recommendations:
                combined_rec.append(rec)

        for rec in content_based_rec:
            if rec[0] not in common_businesses and len(combined_rec) < num_of_recommendations:
                combined_rec.append(rec)

        
        combined_rec.sort(key=lambda x: x[1], reverse=True)

        hybrid_recommendations[user_id] = combined_rec[:5]


    return hybrid_recommendations